In [1]:
from graphein.ml.conversion import GraphFormatConvertor
import numpy as np
import torch
from sklearn.model_selection import train_test_split
from graphein.protein.utils import get_obsolete_mapping
import pandas as pd
import os
from tqdm.notebook import tqdm

/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [2]:
# CONFIGS
import graphein.protein as gp
from functools import partial
from graphein.ml.conversion import GraphFormatConvertor
from graphein.protein.edges.distance import (add_peptide_bonds,
                                             add_hydrogen_bond_interactions,
                                             add_disulfide_interactions,
                                             add_ionic_interactions,
                                             add_aromatic_interactions,
                                             add_aromatic_sulphur_interactions,
                                             add_cation_pi_interactions
                                             )


# 1: Distance-based
dist_edge_func = {"edge_construction_functions": [partial(gp.add_distance_threshold, threshold=5, long_interaction_threshold=0)]}

# 2: Biochemical interactions, select set
select_edge_func = {"edge_construction_functions": [add_peptide_bonds,
                                                    add_hydrogen_bond_interactions,
                                                    add_disulfide_interactions,
                                                    add_ionic_interactions,
                                                    gp.add_salt_bridges]}

# 3: Biochemical interactions, expanded set
all_edge_func = {"edge_construction_functions": [add_peptide_bonds,
                                                 add_aromatic_interactions,
                                                 add_hydrogen_bond_interactions,
                                                 add_disulfide_interactions,
                                                 add_ionic_interactions,
                                                 add_aromatic_sulphur_interactions,
                                                 add_cation_pi_interactions,
                                                 gp.add_hydrophobic_interactions,
                                                 gp.add_vdw_interactions,
                                                 gp.add_backbone_carbonyl_carbonyl_interactions,
                                                 gp.add_salt_bridges]}

In [16]:

# A: Just one-hot encodings
one_hot = {"node_metadata_functions" : [gp.amino_acid_one_hot]}

# B: Selected biochemical features
all_graph_metadata = {"graph_metadata_functions" : [gp.rsa,
                                                    gp.secondary_structure]}
all_node_metadata = {"node_metadata_functions" : [gp.amino_acid_one_hot,
                                                  gp.meiler_embedding,
                                                  partial(gp.expasy_protein_scale, add_separate=True)],
                     "dssp_config": gp.DSSPConfig()
                     }


config_1A = gp.ProteinGraphConfig(**{**dist_edge_func, **one_hot})
config_1B = gp.ProteinGraphConfig(**{**dist_edge_func, **all_graph_metadata, **all_node_metadata})

config_2A = gp.ProteinGraphConfig(**{**select_edge_func, **one_hot})
config_2B = gp.ProteinGraphConfig(**{**select_edge_func, **all_graph_metadata, **all_node_metadata})

config_3A = gp.ProteinGraphConfig(**{**all_edge_func, **one_hot})
config_3B = gp.ProteinGraphConfig(**{**all_edge_func, **all_graph_metadata, **all_node_metadata})

In [15]:

from graphein.ml import InMemoryProteinGraphDataset
import os
# 1: Distance-based
dist_edge_func = {"edge_construction_functions": [partial(gp.add_distance_threshold, threshold=5, long_interaction_threshold=0)]}

# 2: Biochemical interactions, select set
select_edge_func = {"edge_construction_functions": [add_peptide_bonds,
                                                    add_hydrogen_bond_interactions,
                                                    ]}

# 3: Biochemical interactions, expanded set
all_edge_func = {"edge_construction_functions": [add_peptide_bonds,
                                                 add_aromatic_interactions,
                                                 add_hydrogen_bond_interactions,
                                                 add_disulfide_interactions,
                                                 add_ionic_interactions,
                                                 add_aromatic_sulphur_interactions,
                                                 add_cation_pi_interactions,
                                                 gp.add_hydrophobic_interactions,
                                                 gp.add_vdw_interactions,
                                                 gp.add_backbone_carbonyl_carbonyl_interactions,
                                                 gp.add_salt_bridges]}

# A: Just one-hot encodings
one_hot = {"node_metadata_functions" : [gp.amino_acid_one_hot, gp.meiler_embedding,
                                        partial(gp.expasy_protein_scale, add_separate=True)]}

# B: Selected biochemical features
all_graph_metadata = {"graph_metadata_functions" : [gp.rsa,
                                                    gp.secondary_structure]}
all_node_metadata = {"node_metadata_functions" : [gp.amino_acid_one_hot,
                                                  gp.meiler_embedding,
                                                  partial(gp.expasy_protein_scale, add_separate=True)],
                     #"dssp_config": gp.DSSPConfig()
                     }


config_1A = gp.ProteinGraphConfig(**{**dist_edge_func, **one_hot})
config = config_3B #1A is least memory-intensive
convertor = GraphFormatConvertor(src_format="nx", dst_format="pyg", columns=["coords", "edge_index",
                                                                             "amino_acid_one_hot", "bulkiness",
                                                                             "meiler", "rsa", "pka_rgroup",
                                                                             "isoelectric_points",
                                                                             "polaritygrantham",
                                                                             "hphob_black", "transmembranetendency"])

# Get paths to all your PDB files
pdb_dir = os.path.expanduser("~/Downloads/nanobody_extracted")
pdb_paths = [os.path.join(pdb_dir, f) for f in os.listdir(pdb_dir) if f.endswith('.pdb')]

# Create label map (assuming you have a way to determine labels)
# For example, if nanobody in filename means label=1:
label_map = {os.path.splitext(os.path.basename(path))[0]: 1 if "nanobody" in path else 0
             for path in pdb_paths}

# Create the dataset
train_ds = InMemoryProteinGraphDataset(
    root="data/",
    name="train",
    paths=pdb_paths,  # Use paths instead of pdb_codes
    graph_label_map=label_map,
    graphein_config=config_1A,  # Use whichever config you prefer
    graph_format_convertor=convertor,
    graph_transformation_funcs=[],
)

Constructing Graphs...


Processing...
/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/graphein/protein/graphs.py:1014: TqdmWarning: Iterable length 2901 > 1000 but `chunksize` is not set. This may seriously degrade multiprocess performance. Set `chunksize=1` or more.
  process_map(
  0%|          | 0/2901 [00:00<?, ?it/s]/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3

Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Initializing graph...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Initializing graph...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Constructing edges...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━   0% -:--:--

  0%|          | 1/2901 [00:08<6:43:04,  8.34s/it]

Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Initializing graph...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Initializing graph...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Initializing graph...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Constructing edges...       ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         

...

 99%|█████████▉| 2877/2901 [01:45<00:00, 24.77it/s]

Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━���━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe... ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Reading PDB file...         ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Processing PDB dataframe..

100%|██████████| 2901/2901 [01:45<00:00, 27.60it/s]


Transforming Nx Graphs...
Converting Graphs...
Assigning graph Labels...
Saving Data...
Done!


Done!


In [17]:
from torch_geometric.data import DataLoader

train_loader = DataLoader(train_ds, batch_size=4, shuffle=True, drop_last=True)


/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/torch_geometric/deprecation.py:12: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [18]:
for b in train_ds:
    print(b)
    break

Data(edge_index=[2, 425], node_id=[117], coords=[117, 3], amino_acid_one_hot=[117, 20], meiler=[117, 7], pka_rgroup=[117], isoelectric_points=[117], bulkiness=[117], polaritygrantham=[117], hphob_black=[117], transmembranetendency=[117], graph_y=[1], num_nodes=117)


In [19]:
num_proteins = len(train_ds)
print(f"Number of proteins in the dataset: {num_proteins}")

Number of proteins in the dataset: 2901


In [20]:
import pandas as pd

def protein_to_dataframe(protein_data):
    """Convert a PyG protein data object to a pandas DataFrame."""
    data_dict = {}

    # Get number of nodes
    num_nodes = protein_data.num_nodes

    # Add basic node indices
    data_dict['node_idx'] = list(range(num_nodes))

    # Add all available node features
    for key in protein_data.keys:
        attr = getattr(protein_data, key)
        if attr is not None and hasattr(attr, 'shape') and attr.shape[0] == num_nodes:
            # Handle different feature shapes
            if len(attr.shape) == 1:  # Single value per node
                data_dict[key] = attr.tolist()
            elif len(attr.shape) == 2:  # Vector per node
                if key == 'amino_acid_one_hot':
                    # Convert one-hot to amino acid type
                    aa_types = ['ALA', 'ARG', 'ASN', 'ASP', 'CYS', 'GLN', 'GLU', 'GLY', 'HIS', 'ILE',
                                'LEU', 'LYS', 'MET', 'PHE', 'PRO', 'SER', 'THR', 'TRP', 'TYR', 'VAL']
                    aa_indices = attr.argmax(dim=1).tolist()
                    data_dict['amino_acid'] = [aa_types[idx] if idx < len(aa_types) else 'UNK' for idx in aa_indices]
                else:
                    # For other vector features, we can take the mean or list them as strings
                    data_dict[key] = [str(attr[i].tolist()) for i in range(num_nodes)]

    # Create DataFrame
    df = pd.DataFrame(data_dict)
    return df

# Convert first protein to DataFrame and display
protein_df = protein_to_dataframe(train_ds[0])
print(protein_df.head(10))  # Show first 10 residues

   node_idx  pka_rgroup  bulkiness  transmembranetendency  \
0         0       10.28      15.71                  -3.46   
1         1        7.00      21.57                   1.46   
2         2        7.00      14.45                  -1.84   
3         3        7.00      21.40                   1.82   
4         4        7.00      14.45                  -1.84   
5         5        4.25      13.57                  -2.90   
6         6        7.00       9.47                  -0.53   
7         7        7.00       3.40                  -0.19   
8         8        7.00       3.40                  -0.19   
9         9        7.00       3.40                  -0.19   

                                              coords  hphob_black  \
0  [21.917999267578125, 18.42099952697754, 53.969...        0.283   
1  [21.610000610351562, 14.668999671936035, 53.43...        0.825   
2  [21.426000595092773, 12.781999588012695, 56.74...        0.251   
3  [20.67300033569336, 9.0649995803833, 57.123001...

In [21]:
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
import torch
from torch_geometric.data import Data
from collections import Counter
import os

def analyze_protein_dataset(dataset):
    """
    Perform basic analysis of a protein graph dataset from Graphein.
    """
    print(f"Dataset contains {len(dataset)} protein graphs")

    # Available features
    sample = dataset[0]
    print("Available attributes:", [attr for attr in dir(sample) if not attr.startswith('_')])

    # Create output directory
    os.makedirs("protein_analysis", exist_ok=True)

    # Collect statistics
    node_counts = []
    edge_counts = []
    aa_types = []

    # Edge length distribution
    edge_lengths = []

    # Class distribution if available
    class_counts = Counter()

    for i, data in enumerate(dataset):
        # Get node count
        if hasattr(data, 'num_nodes'):
            num_nodes = data.num_nodes
        elif hasattr(data, 'amino_acid_one_hot') and isinstance(data.amino_acid_one_hot, torch.Tensor):
            num_nodes = data.amino_acid_one_hot.shape[0]
        elif hasattr(data, 'coords') and isinstance(data.coords, torch.Tensor):
            num_nodes = data.coords.shape[0]
        else:
            num_nodes = 0

        node_counts.append(num_nodes)

        # Get edge count
        if hasattr(data, 'edge_index') and data.edge_index is not None:
            num_edges = data.edge_index.shape[1]
            edge_counts.append(num_edges)

            # Calculate edge lengths if coordinates are available
            if hasattr(data, 'coords') and data.coords is not None:
                coords = data.coords
                edge_index = data.edge_index

                # Sample up to 100 edges to avoid performance issues
                max_edges = min(100, edge_index.shape[1])
                indices = torch.randperm(edge_index.shape[1])[:max_edges]

                for j in indices:
                    src, dst = edge_index[0, j], edge_index[1, j]
                    length = torch.norm(coords[src] - coords[dst]).item()
                    edge_lengths.append(length)

        # Get class if available
        if hasattr(data, 'graph_y'):
            if isinstance(data.graph_y, torch.Tensor):
                if data.graph_y.dim() > 1:
                    class_label = torch.argmax(data.graph_y).item()
                else:
                    class_label = data.graph_y.item()
                class_counts[class_label] += 1

        # Get amino acid types if one-hot encoding is available
        if hasattr(data, 'amino_acid_one_hot') and isinstance(data.amino_acid_one_hot, torch.Tensor):
            if data.amino_acid_one_hot.dim() > 1:
                aa_indices = torch.argmax(data.amino_acid_one_hot, dim=1).tolist()
                aa_types.extend(aa_indices)

    # 1. Protein size distribution
    plt.figure(figsize=(10, 6))
    sns.histplot(node_counts, bins=20, kde=True)
    plt.title('Distribution of Protein Sizes')
    plt.xlabel('Number of Residues')
    plt.ylabel('Frequency')
    plt.savefig('protein_analysis/protein_size_distribution.png', dpi=300, bbox_inches='tight')
    plt.close()

    # 2. Edge count distribution if available
    if edge_counts:
        plt.figure(figsize=(10, 6))
        sns.histplot(edge_counts, bins=20, kde=True)
        plt.title('Distribution of Edge Counts')
        plt.xlabel('Number of Edges')
        plt.ylabel('Frequency')
        plt.savefig('protein_analysis/edge_count_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

    # 3. Node vs Edge count
    if edge_counts:
        plt.figure(figsize=(10, 6))
        plt.scatter(node_counts, edge_counts, alpha=0.5)
        plt.title('Nodes vs Edges')
        plt.xlabel('Number of Nodes (Residues)')
        plt.ylabel('Number of Edges')

        # Add trend line
        if len(node_counts) > 1:
            z = np.polyfit(node_counts, edge_counts, 1)
            p = np.poly1d(z)
            plt.plot(sorted(node_counts), p(sorted(node_counts)), "r--",
                     label=f"Trend: y={z[0]:.2f}x+{z[1]:.2f}")
            plt.legend()

        plt.savefig('protein_analysis/nodes_vs_edges.png', dpi=300, bbox_inches='tight')
        plt.close()

    # 4. Edge length distribution if available
    if edge_lengths:
        plt.figure(figsize=(10, 6))
        sns.histplot(edge_lengths, bins=20, kde=True)
        plt.title('Distribution of Edge Lengths')
        plt.xlabel('Edge Length (Å)')
        plt.ylabel('Frequency')
        plt.savefig('protein_analysis/edge_length_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

    # 5. Amino acid distribution if available
    if aa_types:
        aa_names = ['ALA', 'ARG', 'ASN', 'ASP', 'CYS', 'GLN', 'GLU', 'GLY', 'HIS', 'ILE',
                    'LEU', 'LYS', 'MET', 'PHE', 'PRO', 'SER', 'THR', 'TRP', 'TYR', 'VAL']

        # Count occurrences
        aa_counts = Counter(aa_types)

        # Create distribution
        labels = []
        values = []
        for i in range(min(len(aa_names), max(aa_counts.keys()) + 1)):
            labels.append(aa_names[i] if i < len(aa_names) else f"Type {i}")
            values.append(aa_counts.get(i, 0))

        plt.figure(figsize=(12, 6))
        plt.bar(labels, values)
        plt.title('Amino Acid Distribution')
        plt.xlabel('Amino Acid Type')
        plt.ylabel('Frequency')
        plt.xticks(rotation=45)
        plt.tight_layout()
        plt.savefig('protein_analysis/amino_acid_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

    # 6. Class distribution if available
    if class_counts:
        labels = list(class_counts.keys())
        values = list(class_counts.values())

        plt.figure(figsize=(10, 6))
        plt.bar(labels, values)
        plt.title('Class Distribution')
        plt.xlabel('Class')
        plt.ylabel('Frequency')
        plt.xticks(labels)
        plt.savefig('protein_analysis/class_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

    # Print summary statistics
    print("\nSummary Statistics:")
    print(f"Total proteins: {len(dataset)}")
    print(f"Average protein size: {np.mean(node_counts):.2f} residues")
    print(f"Min protein size: {min(node_counts)} residues")
    print(f"Max protein size: {max(node_counts)} residues")

    if edge_counts:
        print(f"Average edges per protein: {np.mean(edge_counts):.2f}")
        print(f"Average edge density: {np.mean([e/(n*(n-1)/2) for e, n in zip(edge_counts, node_counts) if n > 1]):.4f}")

    if class_counts:
        print("\nClass distribution:")
        for label, count in sorted(class_counts.items()):
            print(f"  Class {label}: {count} proteins ({count/len(dataset)*100:.1f}%)")

    print("\nAnalysis complete. Figures saved to 'protein_analysis/' directory.")



In [22]:
print(train_ds.len())

2901


In [23]:

stats = analyze_protein_dataset(train_ds)(train_ds)

print("EDA completed. Figures saved to 'protein_eda_figures/' directory.")

Dataset contains 2901 protein graphs
Available attributes: ['apply', 'apply_', 'batch', 'clone', 'coalesce', 'contains_isolated_nodes', 'contains_self_loops', 'contiguous', 'cpu', 'cuda', 'debug', 'detach', 'detach_', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'from_dict', 'has_isolated_nodes', 'has_self_loops', 'is_coalesced', 'is_cuda', 'is_directed', 'is_edge_attr', 'is_node_attr', 'is_undirected', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pin_memory', 'pos', 'record_stream', 'requires_grad_', 'share_memory_', 'size', 'stores', 'stores_as', 'subgraph', 'to', 'to_dict', 'to_heterogeneous', 'to_namedtuple', 'x', 'y']

Summary Statistics:
Total proteins: 2901
Average protein size: 121.04 residues
Min protein size: 91 residues
Max protein size: 142 residues
Average edges per protein: 433.67
Average edge density: 0.0599

Class distribution:
  Class 1: 2901 proteins (100.0%)

Analysis complete. Fi

TypeError: 'NoneType' object is not callable

In [24]:
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
import torch
from collections import Counter
import os

def simple_protein_analysis(dataset):
    """
    Simple and robust analysis of a protein graph dataset.
    Focuses only on the most essential metrics with careful error handling.

    Args:
        dataset: PyTorch Geometric dataset containing protein graphs
    """
    print(f"Dataset contains {len(dataset)} protein graphs")

    # Create output directory
    os.makedirs("protein_analysis", exist_ok=True)

    # Basic statistics
    size_stats = []
    edge_stats = []
    class_labels = []
    aa_counts = Counter()

    # Collect sample of edges and their lengths for analysis
    sample_edges = []

    # Process each protein
    for i in range(len(dataset)):
        data = dataset[i]
        print(f"\nProtein {i}:")

        # Print available attributes
        attrs = [attr for attr in dir(data) if not attr.startswith('_') and not callable(getattr(data, attr))]
        print(f"Available attributes: {attrs}")

        # Get protein size
        size = None
        if hasattr(data, 'num_nodes'):
            size = data.num_nodes
            print(f"Number of nodes: {size}")
        elif hasattr(data, 'amino_acid_one_hot') and isinstance(data.amino_acid_one_hot, torch.Tensor):
            size = data.amino_acid_one_hot.shape[0]
            print(f"Number of nodes (from one-hot): {size}")
        elif hasattr(data, 'coords') and isinstance(data.coords, torch.Tensor):
            size = data.coords.shape[0]
            print(f"Number of nodes (from coords): {size}")

        if size is not None:
            size_stats.append(size)

        # Get edge information
        if hasattr(data, 'edge_index') and isinstance(data.edge_index, torch.Tensor):
            num_edges = data.edge_index.shape[1]
            print(f"Number of edges: {num_edges}")
            edge_stats.append(num_edges)

            # Sample edges for length calculation
            if hasattr(data, 'coords') and isinstance(data.coords, torch.Tensor):
                # Sample up to 10 edges per protein
                edge_index = data.edge_index
                coords = data.coords

                # Get random indices for sampling (up to 10)
                num_samples = min(10, edge_index.shape[1])
                try:
                    indices = torch.randperm(edge_index.shape[1])[:num_samples]

                    for idx in indices:
                        src, dst = edge_index[0, idx], edge_index[1, idx]
                        try:
                            length = torch.norm(coords[src] - coords[dst]).item()
                            sample_edges.append(length)
                        except Exception as e:
                            print(f"  Error calculating edge length: {e}")
                except Exception as e:
                    print(f"  Error sampling edges: {e}")

        # Get class label
        if hasattr(data, 'graph_y') and data.graph_y is not None:
            try:
                if isinstance(data.graph_y, torch.Tensor):
                    if data.graph_y.dim() > 1:
                        label = torch.argmax(data.graph_y).item()
                    else:
                        label = data.graph_y.item()
                    class_labels.append(label)
                    print(f"Class label: {label}")
            except Exception as e:
                print(f"  Error getting class label: {e}")

        # Get amino acid types
        if hasattr(data, 'amino_acid_one_hot') and isinstance(data.amino_acid_one_hot, torch.Tensor):
            try:
                if data.amino_acid_one_hot.dim() > 1:
                    aa_indices = torch.argmax(data.amino_acid_one_hot, dim=1).tolist()
                    aa_counts.update(aa_indices)
                    print(f"Most common amino acid index: {Counter(aa_indices).most_common(1)}")
            except Exception as e:
                print(f"  Error processing amino acid types: {e}")

    # Create visualization for protein sizes
    if size_stats:
        plt.figure(figsize=(10, 6))
        sns.histplot(size_stats, kde=True)
        plt.title('Protein Size Distribution')
        plt.xlabel('Number of Residues')
        plt.ylabel('Frequency')
        plt.savefig('protein_analysis/size_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

        print(f"\nProtein Size Statistics:")
        print(f"  Mean: {np.mean(size_stats):.1f} residues")
        print(f"  Min: {np.min(size_stats)} residues")
        print(f"  Max: {np.max(size_stats)} residues")

    # Create visualization for edge counts
    if edge_stats:
        plt.figure(figsize=(10, 6))
        sns.histplot(edge_stats, kde=True)
        plt.title('Edge Count Distribution')
        plt.xlabel('Number of Edges')
        plt.ylabel('Frequency')
        plt.savefig('protein_analysis/edge_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

        print(f"\nEdge Statistics:")
        print(f"  Mean: {np.mean(edge_stats):.1f} edges per protein")

    # Create visualization for size vs edges
    if size_stats and edge_stats and len(size_stats) == len(edge_stats):
        plt.figure(figsize=(10, 6))
        plt.scatter(size_stats, edge_stats, alpha=0.7)
        plt.title('Protein Size vs Edge Count')
        plt.xlabel('Number of Residues')
        plt.ylabel('Number of Edges')
        plt.savefig('protein_analysis/size_vs_edges.png', dpi=300, bbox_inches='tight')
        plt.close()

    # Create visualization for edge lengths
    if sample_edges:
        plt.figure(figsize=(10, 6))
        sns.histplot(sample_edges, kde=True)
        plt.title('Edge Length Distribution (Sample)')
        plt.xlabel('Edge Length (Å)')
        plt.ylabel('Frequency')
        plt.savefig('protein_analysis/edge_length_sample.png', dpi=300, bbox_inches='tight')
        plt.close()

        print(f"\nEdge Length Statistics (Sample):")
        print(f"  Mean: {np.mean(sample_edges):.2f} Å")
        print(f"  Min: {np.min(sample_edges):.2f} Å")
        print(f"  Max: {np.max(sample_edges):.2f} Å")

    # Create visualization for amino acid distribution
    if aa_counts:
        # Standard amino acid names
        aa_names = ['ALA', 'ARG', 'ASN', 'ASP', 'CYS', 'GLN', 'GLU', 'GLY', 'HIS', 'ILE',
                    'LEU', 'LYS', 'MET', 'PHE', 'PRO', 'SER', 'THR', 'TRP', 'TYR', 'VAL']

        # Prepare data for plotting
        labels = []
        values = []
        for idx in range(min(len(aa_names), max(aa_counts.keys())+1)):
            if idx < len(aa_names):
                labels.append(aa_names[idx])
            else:
                labels.append(f"Type {idx}")
            values.append(aa_counts.get(idx, 0))

        plt.figure(figsize=(12, 6))
        plt.bar(labels, values)
        plt.title('Amino Acid Distribution')
        plt.xlabel('Amino Acid Type')
        plt.ylabel('Frequency')
        plt.xticks(rotation=45)
        plt.tight_layout()
        plt.savefig('protein_analysis/aa_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

        print(f"\nAmino Acid Distribution:")
        total = sum(values)
        for i, (name, count) in enumerate(zip(labels, values)):
            print(f"  {name}: {count} ({count/total*100:.1f}%)")

    # Create visualization for class distribution
    if class_labels:
        class_counter = Counter(class_labels)
        plt.figure(figsize=(8, 5))
        plt.bar(class_counter.keys(), class_counter.values())
        plt.title('Class Distribution')
        plt.xlabel('Class')
        plt.ylabel('Count')
        plt.xticks(list(class_counter.keys()))
        plt.savefig('protein_analysis/class_distribution.png', dpi=300, bbox_inches='tight')
        plt.close()

        print(f"\nClass Distribution:")
        for label, count in sorted(class_counter.items()):
            print(f"  Class {label}: {count} proteins ({count/len(class_labels)*100:.1f}%)")

    print("\nAnalysis complete. Visualizations saved to 'protein_analysis/' directory.")



In [25]:
simple_protein_analysis(train_ds)

Dataset contains 2901 protein graphs

Protein 0:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pos', 'stores', 'x', 'y']
Number of nodes: 117
Number of edges: 425
Class label: 1
Most common amino acid index: [(5, 14)]

Protein 1:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pos', 'stores', 'x', 'y']
Number of nodes: 117
Number of edges: 427
Class label: 1
Most common amino acid index: [(5, 16)]

Protein 2:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pos', 'stores', 'x

/Users/alexchilton/PycharmProjects/final_try copy/.venv/lib/python3.9/site-packages/torch_geometric/deprecation.py:12: UserWarning: 'num_faces' is deprecated, use 'data.face.size(-1)' instead
  warnings.warn(out)


Class label: 1
Most common amino acid index: [(15, 17)]

Protein 735:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pos', 'stores', 'x', 'y']
Number of nodes: 128
Number of edges: 468
Class label: 1
Most common amino acid index: [(5, 16)]

Protein 736:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_nodes', 'pos', 'stores', 'x', 'y']
Number of nodes: 122
Number of edges: 438
Class label: 1
Most common amino acid index: [(15, 15)]

Protein 737:
Available attributes: ['batch', 'edge_attr', 'edge_index', 'edge_stores', 'edge_weight', 'is_cuda', 'keys', 'node_stores', 'num_edge_features', 'num_edges', 'num_faces', 'num_features', 'num_node_features', 'num_n